# Spoken Language Recognition Using Convolutional Neural Networks

_written by Joscha S. Rieber (Fraunhofer IAIS) in 2020_

## Dataset preparation

Please go to the [Mozilla Common Voice Website](https://commonvoice.mozilla.org/) and download the full German and English datasets. In the following scripts we will thin out the datasets to make them more handy and play with the data.
* Download German and English datasets
* Extract them
* Define paths below

In [1]:
train = 'train'
test = 'test'

eng = 'english'
ger = 'german'
swe = 'swedish'

languages = [eng, ger, swe]
categories = [train, test]

original_dataset_paths = {}

original_dataset_paths[eng] = 'D:/voiceData/cv-corpus-10.0-2022-07-04/en/' # TODO: Adapt this folder!
original_dataset_paths[ger] = 'D:/voiceData/cv-corpus-10.0-2022-07-04/de/' # TODO: Adapt this folder!
original_dataset_paths[swe] = 'D:/voiceData/cv-corpus-10.0-2022-07-04/sv/' # TODO: Adapt this folder!

target_root_path = '../data/'

num_files_to_take_for_each_language = 2000 # 20000 is the maximum number of files for each language
train_rate = 0.8  # Use 80 % of the data for training and the rest for testing

In [2]:
target_root_path

'../data/'

In [3]:
import os
for lang in languages:
    if not os.path.isdir(original_dataset_paths[lang]):
        raise
    for category in categories:
        if not os.path.isdir(target_root_path + category + '/' + lang):
            os.makedirs(target_root_path + category + '/' + lang)

### Check paths

If something goes wrong here, check paths again and read the documentation of the GitHub repository and check how to set-up your environment correctly

In [4]:
import os

for lang in languages:
    if not os.path.isdir(original_dataset_paths[lang]):
        raise
    for category in categories:
        if not os.path.isdir(target_root_path + category + '/' + lang):
            raise

for lang in languages:
    if not os.path.isfile(original_dataset_paths[lang] + 'validated.tsv'):
        raise
    if not os.path.isdir(original_dataset_paths[lang] + 'clips'):
        raise

Collect only num_files_to_take_for_each_language files which duration is between 7.5 and 10 seconds

<span style="color:red">Note, that this process might take many hours!</span>

In [7]:
# If this goes wrong, check your environment and read the documentation

import librosa as lr
from glob import glob
from random import shuffle
from shutil import copy2
import numpy as np
import pandas as pd
import warnings
import soundfile as sf

In [8]:
def copy_audio_files_for_language(lang):
    
    print('')
    print('Copying files for language ' + lang + '...')
    print('')
    
    # Only take validated speech data
    df = pd.read_csv(original_dataset_paths[lang] + 'validated.tsv', sep='\t', low_memory=False)
    all_filenames = df['path'].tolist()
    shuffle(all_filenames)
    
    counter = 0
    
    category = train    
    
    # Process files
    for filename in all_filenames:
        file = original_dataset_paths[lang] + 'clips/' + filename
        try:
            # sound = AudioSegment.from_file(file, format="mp3")
            # wavSound = file.rstrip(".mp3") + ".wav"
            # sound.export(wavSound, format="wav")
            audio_segment, sample_rate = lr.load(file)
            if np.count_nonzero(audio_segment) == 0:
                raise Exception('Audio is silent!')
            if audio_segment.ndim != 1:
                raise Exception('Audio signal has wrong number of dimensions: ' + str(audio_segment.ndim))
            duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
        except Exception as e:
            print('WARNING! Error while loading file \"' + file + '\": ' + str(e) + ' - Skipping...')
            continue
        
        # Only copy audio files with a certain minimum duration
        if 7.5 < duration_sec < 10.0:
            copy2(file, target_root_path + category + '/' + lang)
            counter += 1
        
        # Stop after collecting enough files
        if counter == int(num_files_to_take_for_each_language * train_rate):
            category = test
        if counter == num_files_to_take_for_each_language:
            break

Copy files to create the German language train and test datasets

In [64]:
warnings.simplefilter('ignore', UserWarning)

copy_audio_files_for_language(ger)

warnings.simplefilter('default', UserWarning)


Copying files for language german...

WARNING! Error while loading file "D:/voiceData/cv-corpus-10.0-2022-07-04/de/clips/common_voice_de_18194352.mp3": [Errno 2] No such file or directory: 'D:/voiceData/cv-corpus-10.0-2022-07-04/de/clips/common_voice_de_18194352.mp3' - Skipping...
WARNING! Error while loading file "D:/voiceData/cv-corpus-10.0-2022-07-04/de/clips/common_voice_de_32365523.mp3": [Errno 2] No such file or directory: 'D:/voiceData/cv-corpus-10.0-2022-07-04/de/clips/common_voice_de_32365523.mp3' - Skipping...
WARNING! Error while loading file "D:/voiceData/cv-corpus-10.0-2022-07-04/de/clips/common_voice_de_20117382.mp3": [Errno 2] No such file or directory: 'D:/voiceData/cv-corpus-10.0-2022-07-04/de/clips/common_voice_de_20117382.mp3' - Skipping...
WARNING! Error while loading file "D:/voiceData/cv-corpus-10.0-2022-07-04/de/clips/common_voice_de_18191626.mp3": [Errno 2] No such file or directory: 'D:/voiceData/cv-corpus-10.0-2022-07-04/de/clips/common_voice_de_18191626.mp3'

KeyboardInterrupt: 

Copy files to create the English language train and test datasets

In [6]:
warnings.simplefilter('ignore', UserWarning)

copy_audio_files_for_language(eng)

warnings.simplefilter('default', UserWarning)


Copying files for language english...

WARNING! Error while loading file "/data/jrieber/IFINDER-2143/common-voice/cv-corpus-5.1-2020-06-22/en/clips/common_voice_en_190149.mp3": Audio is silent! - Skipping...


In [ ]:
warnings.simplefilter('ignore', UserWarning)

copy_audio_files_for_language(swe)

warnings.simplefilter('default', UserWarning)


Copying files for language swedish...



C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[0. 0. 0. ... 0. 0. 0.] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  9.7519978e-07
 -9.3858154e-07  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.000000e+00  0.000000e+00  0.000000e+00 ... -7.881404e-08  5.104326e-08
  0.000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppDa

C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ... -9.9369073e-09
  5.1352522e-09 -1.5974889e-09] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 2.9435319e-07 7.6045825e-07
 0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ... -3.8619123e-06
  2.3604139e-06  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec =

C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ... -1.0664522e-05
 -4.9292361e-05  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ... -1.6127589e-05
 -2.9854365e-05  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.000000e+00  0.000000e+00  0.000000e+00 ... -1.822268e-08  7.275083e-09
  0.000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec =

C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 1.4881801e-04 3.9331971e-05
 0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  1.8905268e-05
 -7.2069153e-05  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ... -3.8032559e-09
  2.4238302e-09  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec =

...

C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ... -6.1166801e-08
  5.2118782e-08  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ... -5.6924016e-08
  4.0742329e-08  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ... -9.4727538e-06
  1.2762896e-05  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration

C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  1.6239465e-08
 -1.3607068e-08  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  3.4826953e-05
 -1.8847513e-06  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  1.7246239e-09
 -1.7637478e-09  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration

C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  3.7668722e-06
 -8.3388426e-07  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  5.3659005e-05
 -9.4233837e-06  2.3134153e-06] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ... -1.2593019e-05
 -3.0967211e-08  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration

C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.000000e+00  0.000000e+00  0.000000e+00 ... -8.810664e-07 -9.041234e-08
  0.000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ...  2.2420272e-09
 -2.5566864e-09  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.000000e+00  0.000000e+00  0.000000e+00 ... -1.871909e-05 -8.398229e-06
  0.000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.co

C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ... -1.3709456e-06
 -3.5192199e-05  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ... -1.4931968e-05
 -1.8747089e-05  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration_sec = lr.core.get_duration(audio_segment, sr=sample_rate)
C:\Users\filip\AppData\Local\Temp/ipykernel_26644/3898932360.py:28: FutureWarning: Pass y=[ 0.0000000e+00  0.0000000e+00  0.0000000e+00 ... -1.5102161e-07
  1.3630762e-07  0.0000000e+00] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  duration

In [ ]:
# import common_voice_de_17298952.mp3 from src using librosa as lr
file = 'D:/voiceData/cv-corpus-10.0-2022-07-04/sv/clips/common_voice_sv-SE_18710562.mp3'

audio_segment, sample_rate = sf.read(file)



### Check number of collected files

In [7]:
for category in categories:
    
    if category == train:
        num_files = int(num_files_to_take_for_each_language * train_rate)
    else:
        num_files = int(num_files_to_take_for_each_language * (1.0 - train_rate))
        
    for lang in languages:
        folder = target_root_path + category + '/' + lang + '/'
        all_files = glob(folder + '*.mp3')
        
        if len(all_files) < (num_files - 1):
            raise Exception('Folder \"' + folder + '\" only contains ' + str(len(all_files)) + ' files instead of ' + str(num_files) + '!')
            
print('Okay!')

Okay!


Now make yourself familiar with the dataset by listening to some of the files

## Statistics

In [8]:
warnings.simplefilter('ignore', UserWarning)

for category in categories:
    for lang in languages:
        duration_sec = 0.0
        
        folder = target_root_path + category + '/' + lang + '/'
        all_files = glob(folder + '*.mp3')
        
        for file in all_files:
            duration_sec += lr.core.get_duration(filename=file)
            
        duration_h = duration_sec / 60.0 / 60.0
        print('Total duration of ' + lang + ' ' + category + ' is ' + str(round(duration_h, 1)) + ' h')
        
warnings.simplefilter('default', UserWarning)

Total duration of english train is 37.0 h
Total duration of german train is 37.0 h
Total duration of english test is 9.2 h
Total duration of german test is 9.3 h
